# Fetch Rewards Coding Exercise - Alisha Gonsalves

Step 1: Structured Data Model
- Created using dbdiagram (refer 'RelationalDataModel.png)
- After thoroughly analyzing the raw, unstructured data and reviewing the business case, I identified that the RECEIPTS data contains nested column. This nested column, upon extraction, is related to the ITEMS table, representing individual receipt items.
- For the purpose of this coding exercise, I have included only the relevant columns in the data model to maintain focus and clarity. This approach ensures that the exercise remains concise while addressing the core requirements effectively. If additional details are needed, they can be incorporated as the analysis progresses.

In [2]:
%pip install pandas

Note: you may need to restart the kernel to use updated packages.


In [3]:
import json
import pandas as pd
from pandas import json_normalize
from datetime import datetime
import sqlite3


/var/folders/9x/gq8b5q891szb8grfyvmn8hnw0000gn/T/ipykernel_50232/2753723541.py:2: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [4]:
def json_to_tables(data_file_loc, output_excel_file):
    # Read JSON data from file
    with open(data_file_loc, 'r') as file:
        data = [json.loads(line) for line in file]
    
    # Flatten JSON data
    df = json_normalize(data)
    
    # Handle missing keys by filling NaN with None
    df = df.where(pd.notnull(df), None)
    
    # Save the DataFrame to an Excel file
    df.to_excel(output_excel_file, index=False)

json_to_tables('brands.json', 'brands.xlsx')
json_to_tables('receipts.json', 'receipts.xlsx')
json_to_tables('users.json', 'users.xlsx')


Step 2: Data Cleaning
1. USERS table
- Reading the "users" Excel file into a DataFrame below.
- Transforming specific columns to appropriate data types.
- Renaming few columns and removing rows with missing or duplicate `userId` values.

In [5]:
# Read the Excel file
df = pd.read_excel('users.xlsx')

# Convert columns to appropriate data types
df['_id.$oid'] = df['_id.$oid'].astype(str)
df['createdDate.$date'] = pd.to_datetime(df['createdDate.$date'], unit='ms')
df['lastLogin.$date'] = pd.to_datetime(df['lastLogin.$date'], unit='ms')
df['active'] = df['active'].astype(bool)

# Save the corrected DataFrame back to an Excel file
df.rename(columns={
    '_id.$oid': 'userId',
    'createdDate.$date': 'createdDate',
    'lastLogin.$date': 'lastLogin'
}, inplace=True)
df = df.dropna(subset=['userId'])
df = df.drop_duplicates(subset=['userId'])
df.to_excel('users_corrected.xlsx', index=False)
print(df.dtypes)

active                    bool
role                    object
signUpSource            object
state                   object
userId                  object
createdDate     datetime64[ns]
lastLogin       datetime64[ns]
dtype: object


2. BRANDS table
- Reading the "brands" Excel file into a DataFrame below.
- Transforming specific columns to appropriate data types.
- Renaming few columns and removing rows with missing or duplicate `brand_id` values.

In [6]:
# Read the Excel file
df = pd.read_excel('brands.xlsx')

# Convert columns to appropriate data types
df['barcode'] = df['barcode'].astype(str)
df['topBrand'] = df['topBrand'].astype(bool)
df['_id.$oid'] = df['_id.$oid'].astype(str)
df['cpg.$id.$oid'] = df['cpg.$id.$oid'].astype(str)
df['cpg.$ref'] = df['cpg.$ref'].astype(str)

df.rename(columns={
    '_id.$oid': 'brand_id',
    'cpg.$id.$oid': 'cpg_id',
    'cpg.$ref': 'cpg_ref'
}, inplace=True)
df = df.dropna(subset=['brand_id'])
df = df.drop_duplicates(subset=['brand_id'])
# Save the corrected DataFrame back to an Excel file
df.to_excel('brands_corrected.xlsx', index=False)
print(df.dtypes)

barcode         object
category        object
categoryCode    object
name            object
topBrand          bool
brand_id        object
cpg_id          object
cpg_ref         object
brandCode       object
dtype: object


3.A RECEIPTS table
- Reading the "receipts" Excel file into a DataFrame below.
- Transforming specific columns to appropriate data types including numeric and handling errors by coercing invalid values to `NaN`. 
- Renaming few columns, cleaning date columns to handle overflow issues and removing rows with missing or duplicate `receipt_id` values.

In [7]:
import pandas as pd

# Read the Excel file
df = pd.read_excel('receipts.xlsx')

# Convert columns to appropriate data types
df['bonusPointsEarned'] = pd.to_numeric(df['bonusPointsEarned'], errors='coerce')
df['pointsEarned'] = pd.to_numeric(df['pointsEarned'], errors='coerce')
df['purchasedItemCount'] = pd.to_numeric(df['purchasedItemCount'], errors='coerce')
# df['purchasedItemCount'] = df['purchasedItemCount'].fillna(0).astype(int)
df['totalSpent'] = pd.to_numeric(df['totalSpent'], errors='coerce')
#df['totalSpent'] = df['totalSpent'].fillna(0)


df['rewardsReceiptItemList'] = df['rewardsReceiptItemList'].astype(str)
df['rewardsReceiptStatus'] = df['rewardsReceiptStatus'].astype(str)
df['userId'] = df['userId'].astype(str)
df['_id.$oid'] = df['_id.$oid'].astype(str)

date_columns = ['createDate.$date', 'dateScanned.$date', 'finishedDate.$date', 'modifyDate.$date', 'pointsAwardedDate.$date', 'purchaseDate.$date']
# Inspect and clean date columns to handle overflow issues
for col in date_columns:
    df[col] = pd.to_numeric(df[col], errors='coerce')
    df = df[df[col].between(0, 1e18) | df[col].isna()]  # Filter out unrealistic values
    df[col] = pd.to_datetime(df[col], unit='ms', errors='coerce')

df.rename(columns={
    '_id.$oid': 'receipt_id',
    'createDate.$date': 'createDate',
    'dateScanned.$date': 'dateScanned',
    'finishedDate.$date': 'finishedDate',
    'modifyDate.$date': 'modifyDate',
    'pointsAwardedDate.$date': 'pointsAwardedDate',
    'purchaseDate.$date': 'purchaseDate'
}, inplace=True)

df = df.dropna(subset=['receipt_id'])
df = df.drop_duplicates(subset=['receipt_id'])



# # Exclude rows with negative values in specified numeric columns
# numeric_columns = ['bonusPointsEarned', 'pointsEarned', 'purchasedItemCount', 'totalSpent']
# for col in numeric_columns:
#     df = df[df[col] >= 0]

# Save the corrected DataFrame back to an Excel file
df.to_excel('receipts_corrected.xlsx', index=False)
print(df.dtypes)

bonusPointsEarned                 float64
bonusPointsEarnedReason            object
pointsEarned                      float64
purchasedItemCount                float64
rewardsReceiptItemList             object
rewardsReceiptStatus               object
totalSpent                        float64
userId                             object
receipt_id                         object
createDate                 datetime64[ns]
dateScanned                datetime64[ns]
finishedDate               datetime64[ns]
modifyDate                 datetime64[ns]
pointsAwardedDate          datetime64[ns]
purchaseDate               datetime64[ns]
dtype: object


3.B Extracting the nested data from RECEIPTS table
- Processing json_to_table function to extract and normalize rewards item column.
- Skips duplicate receipt_id's to avoid data redundancy.
- Adding user_id and receipt_id to each reward item to simplify relation between the tables.

In [8]:
def json_to_tables(data_file_loc):
    list_of_full_items = []
    processed_receipt_ids = set()
    
    try:
        # Read JSON data from file
        with open(data_file_loc, 'r') as file:
            data = [json.loads(line) for line in file]
            print(f"Successfully read data from {data_file_loc}")

            for item in data:
                reciept_id = item.get('_id', None)
                if reciept_id:
                    reciept_id = reciept_id.get("$oid", None)
                
                # Skip if receipt_id is duplicate
                if reciept_id in processed_receipt_ids:
                    print(f"Skipping duplicate receiptId: {reciept_id}")
                    continue
                
                # Add receipt_id to the set of processed ids
                processed_receipt_ids.add(reciept_id)

                list_of_reward = item.get('rewardsReceiptItemList', [])
                user_id = item.get('userId', None)

                # Add user_id and reciept_id to each reward item
                for reward in list_of_reward:
                    reward['userId'] = user_id
                    reward['receipt_id'] = reciept_id

                list_of_full_items.extend(list_of_reward)

                print(f"Appended rewardsReceiptItemList: {list_of_reward}")
                print(f"Appended userId: {user_id}")
                print(f"Appended receiptId: {reciept_id}")

    except Exception as e:
        print(f"Error reading or processing file {data_file_loc}: {e}")

    return list_of_full_items

rewards_list = json_to_tables('receipts.json')
print(f"Extracted rewards list: {rewards_list}")

# Flatten the nested list (already flattened in the function)
flattened_rewards_list = rewards_list
print(f"Flattened rewards list: {flattened_rewards_list}")

# Normalize the flattened data
normalized_df = pd.json_normalize(flattened_rewards_list)
print(f"Normalized DataFrame:\n{normalized_df}")

# Display the resulting DataFrame
print(normalized_df)

# Save the new table to an Excel file
normalized_df.to_excel('normalized_receipts_new.xlsx', index=False)
print("Saved normalized data to normalized_receipts_new.xlsx")

Successfully read data from receipts.json
Appended rewardsReceiptItemList: [{'barcode': '4011', 'description': 'ITEM NOT FOUND', 'finalPrice': '26.00', 'itemPrice': '26.00', 'needsFetchReview': False, 'partnerItemId': '1', 'preventTargetGapPoints': True, 'quantityPurchased': 5, 'userFlaggedBarcode': '4011', 'userFlaggedNewItem': True, 'userFlaggedPrice': '26.00', 'userFlaggedQuantity': 5, 'userId': '5ff1e1eacfcf6c399c274ae6', 'receipt_id': '5ff1e1eb0a720f0523000575'}]
Appended userId: 5ff1e1eacfcf6c399c274ae6
Appended receiptId: 5ff1e1eb0a720f0523000575
Appended rewardsReceiptItemList: [{'barcode': '4011', 'description': 'ITEM NOT FOUND', 'finalPrice': '1', 'itemPrice': '1', 'partnerItemId': '1', 'quantityPurchased': 1, 'userId': '5ff1e194b6a9d73a3a9f1052', 'receipt_id': '5ff1e1bb0a720f052300056b'}, {'barcode': '028400642255', 'description': 'DORITOS TORTILLA CHIP SPICY SWEET CHILI REDUCED FAT BAG 1 OZ', 'finalPrice': '10.00', 'itemPrice': '10.00', 'needsFetchReview': True, 'needsFetch

4. ITEMS table
- Reading the "normalized_receipts_new" Excel file into a DataFrame below.
- Transforming specific columns to appropriate data types including numeric and boolean types.
- Adding a new column 'receipt_item_id' where each row is assigned to a unique UUID.
- Dropped few columns which are not required for the purpose of this analysis, we can skip this process when dealing with different business problem.

This code also performs the following steps:

1. Initializes three empty collections: `actual_quantity_by_receipt`, `actual_final_price_by_receipt`, and `item_price_list`.
2. Iterates over each row in the DataFrame `df`:
   - Updates `actual_quantity_by_receipt` with the sum of `quantityPurchased` for each `receipt_id`.
   - Updates `actual_final_price_by_receipt` with the sum of `finalPrice` for each `receipt_id`.
   - Calculates the item price by dividing `finalPrice` by `quantityPurchased` and appends it to `item_price_list`. If an exception occurs, it appends `None` and prints an error message.
3. Adds the `item_price_list` as a new column `actual_item_price` in `df`.
4. Reads another DataFrame `df_receipts` from the receipts_corrected Excel file.
5. Maps `actual_quantity_by_receipt` to `df_receipts` based on `receipt_id` and fills `NaN` values with `purchasedItemCount`.
6. Maps `actual_final_price_by_receipt` to `df_receipts` based on `receipt_id` and fills `NaN` values with `totalSpent`.

In [9]:
import pandas as pd
import uuid

# Read the Excel file
df = pd.read_excel('normalized_receipts_new.xlsx')

# Convert columns to appropriate data types
df['barcode'] = df['barcode'].astype(str)
df['partnerItemId'] = df['partnerItemId'].astype(str)
df['userId'] = df['userId'].astype(str)
df['receipt_id'] = df['receipt_id'].astype(str)

numeric_columns = ['finalPrice', 'itemPrice', 'quantityPurchased', 'userFlaggedPrice', 'userFlaggedQuantity', 'discountedItemPrice', 'targetPrice', 'originalFinalPrice', 'originalMetaBriteItemPrice', 'priceAfterCoupon']
for col in numeric_columns:
    df[col] = pd.to_numeric(df[col], errors='coerce')

boolean_columns = ['needsFetchReview', 'preventTargetGapPoints', 'userFlaggedBarcode', 'userFlaggedNewItem', 'competitiveProduct', 'deleted']
for col in boolean_columns:
    df[col] = df[col].astype(bool)

#df['quantityPurchased'] = df['quantityPurchased'].fillna(0).astype(int)

# # Exclude rows with negative values in specified numeric columns
# for col in numeric_columns:
#     df = df[df[col].notna() & (df[col] >= 0)]

# Add UUID to each row
df['receipt_item_id'] = [uuid.uuid4() for _ in range(len(df))]

columns_to_drop = [
    "needsFetchReview",
    "partnerItemId",
    "preventTargetGapPoints",
    "userFlaggedBarcode",
    "userFlaggedNewItem",
    "userFlaggedPrice",
    "userFlaggedQuantity",
    "needsFetchReviewReason",
    "pointsNotAwardedReason",
    "rewardsGroup",
    "userFlaggedDescription",
    "originalMetaBriteBarcode",
    "originalMetaBriteDescription",
    "brandCode",
    "competitorRewardsGroup",
    "discountedItemPrice",
    "originalReceiptItemText",
    "itemNumber",
    "originalMetaBriteQuantityPurchased",
    "pointsEarned",
    "targetPrice",
    "competitiveProduct",
    "originalFinalPrice",
    "originalMetaBriteItemPrice",
    "deleted",
    "priceAfterCoupon",
    "metabriteCampaignId"
]

# Drop the specified columns
df.drop(columns=columns_to_drop, inplace=True)

actual_quantity_by_receipt = {}
actual_final_price_by_receipt = {}
item_price_list = []
for index, row in df.iterrows():
    if row['receipt_id'] not in actual_quantity_by_receipt:
        actual_quantity_by_receipt[row['receipt_id']] = row['quantityPurchased']
    else:
        actual_quantity_by_receipt[row['receipt_id']] += row['quantityPurchased']

    if row['receipt_id'] not in actual_final_price_by_receipt:
        actual_final_price_by_receipt[row['receipt_id']] = row['finalPrice']
    else:
        actual_final_price_by_receipt[row['receipt_id']] += row['finalPrice']

    try:
        if row['itemPrice']:
            item_price_list.append(row['finalPrice']/row['quantityPurchased'])
        else:
            item_price_list.append(None)
    except:
        print(f'exception occured')
        item_price_list.append(None)

df['actual_item_price'] = item_price_list

df_receipts = pd.read_excel('receipts_corrected.xlsx')
df_receipts['actual_purchasedItemCount'] = df_receipts['receipt_id'].map(actual_quantity_by_receipt)
df_receipts['actual_purchasedItemCount'] = df_receipts['actual_purchasedItemCount'].fillna(df_receipts['purchasedItemCount'])

df_receipts['actual_finalPrice'] = df_receipts['receipt_id'].map(actual_final_price_by_receipt)
df_receipts['actual_finalPrice'] = df_receipts['actual_finalPrice'].fillna(df_receipts['totalSpent'])


df_receipts.to_excel('receipts_corrected.xlsx', index=False)

# Save the corrected DataFrame back to an Excel file
df.to_excel('normalized_receipts_new_corrected.xlsx', index=False)
print(df.dtypes)

barcode                     object
description                 object
finalPrice                 float64
itemPrice                  float64
quantityPurchased          float64
userId                      object
receipt_id                  object
pointsPayerId               object
rewardsProductPartnerId     object
receipt_item_id             object
actual_item_price          float64
dtype: object


Establishing a SQLite database connection to analyze the data and address several concerns of the business stakeholder.

In [10]:
# Read the Excel files into DataFrames
df1 = pd.read_excel('users_corrected.xlsx')
df2 = pd.read_excel('brands_corrected.xlsx')
df3 = pd.read_excel('receipts_corrected.xlsx')
df4 = pd.read_excel('normalized_receipts_new_corrected.xlsx')

# Connect to SQLite database (create if it doesn't exist)
conn = sqlite3.connect('my_fetch.db')

# Write DataFrames to tables in the SQLite database
df1.to_sql('users', conn, if_exists='replace', index=False)
df2.to_sql('brands', conn, if_exists='replace', index=False)
df3.to_sql('receipts', conn, if_exists='replace', index=False)
df4.to_sql('items', conn, if_exists='replace', index=False)

6941

In [11]:
# Select all data from items
query = "SELECT * FROM items"
result = pd.read_sql_query(query, conn)

# Print the result of the query
print(result)


           barcode                                        description  \
0             4011                                     ITEM NOT FOUND   
1             4011                                     ITEM NOT FOUND   
2     028400642255  DORITOS TORTILLA CHIP SPICY SWEET CHILI REDUCE...   
3             None                                               None   
4             4011                                     ITEM NOT FOUND   
...            ...                                                ...   
6936    B07BRRLSVC  thindust summer face mask - sun protection nec...   
6937    B076FJ92M4  mueller austria hypergrind precision electric ...   
6938    B07BRRLSVC  thindust summer face mask - sun protection nec...   
6939    B076FJ92M4  mueller austria hypergrind precision electric ...   
6940    B07BRRLSVC  thindust summer face mask - sun protection nec...   

      finalPrice  itemPrice  quantityPurchased                    userId  \
0          26.00      26.00                5.0 

STEP 3: SQL Queries

1] What are the top 5 brands by receipts scanned for most recent month?
- To address the question, I analyzed the data and identified that the most recent available date was March 1st, 2022. Based on this, I determined the latest month's data to provide accurate solutions.
- Since there is no direct relationship between the brands and receipts tables, I thoroughly examined all columns in the items, receipts, and brands tables. I identified and utilized the only two matching columns suitable for joining.
- If transactional data is updated daily, we can directly query the most recent month's data without the need to track the latest available date manually.
- Using dense rank to get top 5 brands as the count for many brands is the same.

In [12]:
query = """
WITH PreviousMonth AS (
    SELECT
        DATE(MAX(dateScanned), '-1 month') AS prev_month_date
    FROM
        receipts
),
PreviousMonthReceipts AS (
    SELECT
        r.receipt_id,
        r.dateScanned,
        i.rewardsProductPartnerId
    FROM
        receipts r
    JOIN
        items i
    ON
        r.receipt_id = i.receipt_id
    WHERE
        DATE(r.dateScanned, 'start of month') = (SELECT DATE(prev_month_date, 'start of month') FROM PreviousMonth)
),
BrandReceipts AS (
    SELECT
        pm.rewardsProductPartnerId,
        COALESCE(b.name, 'Unknown') AS brand_name,
        COUNT(DISTINCT pm.receipt_id) AS receipt_count
    FROM
        PreviousMonthReceipts pm
    INNER JOIN
        brands b
    ON
        pm.rewardsProductPartnerId = b.cpg_id
    GROUP BY
        pm.rewardsProductPartnerId, b.name
),
RankedBrandReceipts AS (
    SELECT
        brand_name,
        receipt_count,
        DENSE_RANK() OVER (ORDER BY receipt_count DESC) AS rank
    FROM
        BrandReceipts
)
SELECT
    brand_name,
    receipt_count
FROM
    RankedBrandReceipts
WHERE
    rank <= 5
ORDER BY
    rank;
"""
result = pd.read_sql_query(query, conn)
#result = result.drop_duplicates()
#result.to_excel('output.xlsx')
# Print the result of the query
print(len(result))
print(result)

271
               brand_name  receipt_count
0                    A.1.              7
1          Amazing Grains              7
2                 Athenos              7
3                 BIAGLUT              7
4    Back to Nature Meals              7
..                    ...            ...
266   THE RIGHT TO SHOWER              2
267                  TIGI              2
268              TONI&GUY              2
269              TRESEMME              2
270              VASELINE              2

[271 rows x 2 columns]


2] How does the ranking of the top 5 brands by receipts scanned for the recent month compare to the ranking for the previous month?
- The query calculates the current and previous month's date ranges in a single CTE (DateRanges). 
- Next, retrieve all relevant receipt data (ReceiptsData), assigning a month_type (Current or Previous) based on the date range. - - The data is later grouped by brand in BrandReceipts, calculating the receipt count for each brand per month type. 
- The RankedBrandReceipts CTE assigns ranks to brands within each month based on receipt counts. 
- Finally, the query compares the top 5 brands from the current month with their performance in the previous month, displaying the receipt counts and ranks for both periods.

In [13]:
query = """
WITH DateRanges AS (
    SELECT
        DATE(MAX(dateScanned), 'start of month', '-1 month') AS current_month_start,
        DATE(MAX(dateScanned), 'start of month', '-2 month') AS prev_month_start
    FROM
        receipts
),
ReceiptsData AS (
    SELECT
        r.receipt_id,
        r.dateScanned,
        i.rewardsProductPartnerId,
        CASE
            WHEN r.dateScanned >= dr.current_month_start 
                 AND r.dateScanned < DATE(dr.current_month_start, '+1 month')
            THEN 'Current'
            WHEN r.dateScanned >= dr.prev_month_start 
                 AND r.dateScanned < DATE(dr.prev_month_start, '+1 month')
            THEN 'Previous'
        END AS month_type
    FROM
        receipts r
    JOIN
        items i
    ON
        r.receipt_id = i.receipt_id
    CROSS JOIN
        DateRanges dr
    WHERE
        r.dateScanned >= dr.prev_month_start
),
BrandReceipts AS (
    SELECT
        rd.month_type,
        rd.rewardsProductPartnerId,
        COALESCE(b.name, 'Unknown') AS brand_name,
        COUNT(DISTINCT rd.receipt_id) AS receipt_count
    FROM
        ReceiptsData rd
    INNER JOIN
        brands b
    ON
        rd.rewardsProductPartnerId = b.cpg_id
    GROUP BY
        rd.month_type, rd.rewardsProductPartnerId, b.name
),
RankedBrandReceipts AS (
    SELECT
        brand_name,
        receipt_count,
        month_type,
        DENSE_RANK() OVER (PARTITION BY month_type ORDER BY receipt_count DESC) AS rank
    FROM
        BrandReceipts
)
SELECT
    cm.brand_name,
    cm.receipt_count AS current_month_receipt_count,
    cm.rank AS current_month_rank,
    pm.receipt_count AS previous_month_receipt_count,
    pm.rank AS previous_month_rank
FROM
    RankedBrandReceipts cm
LEFT JOIN
    RankedBrandReceipts pm
ON
    cm.brand_name = pm.brand_name
   AND pm.month_type = 'Previous'
WHERE
    cm.month_type = 'Current'
    AND cm.rank <= 5
ORDER BY
    cm.rank;
"""
result = pd.read_sql_query(query, conn)
#result = result.drop_duplicates()
#result.to_excel('output.xlsx')
# Print the result of the query
print(len(result))
print(result)

274
               brand_name  current_month_receipt_count  current_month_rank  \
0                    A.1.                            7                   1   
1          Amazing Grains                            7                   1   
2                 Athenos                            7                   1   
3                 BIAGLUT                            7                   1   
4    Back to Nature Meals                            7                   1   
..                    ...                          ...                 ...   
269   THE RIGHT TO SHOWER                            2                   5   
270                  TIGI                            2                   5   
271              TONI&GUY                            2                   5   
272              TRESEMME                            2                   5   
273              VASELINE                            2                   5   

     previous_month_receipt_count  previous_month_rank  
0 

3] When considering average spend from receipts with 'rewardsReceiptStatus’ of ‘Accepted’ or ‘Rejected’, which is greater?
- The query calculates the average spend for receipts, categorizing them as either 'Accepted' or 'Rejected'.
- Using 'actual_finalPrice' as the column to calculate the average spend because the 'totalSpent' column in RECEIPTS table had few data discrepancies.
- Here the logic used is: 'Accepted' status is assigned when rewardsReceiptStatus is one of 'FINISHED', 'SUBMITTED', 'FLAGGED', or 'PENDING' and pointsAwardedDate is not null.
- 'Rejected' status is assigned to receipts where 'rewardsReceiptStatus' is 'Rejecetd'
- The WHERE clause filters records to include only receipts that meet either the 'Accepted' conditions or have a 'REJECTED' status. The query then groups results by receipt_status and computes the average spend for each group.
- The average spend from receipts with 'rewardsReceiptStatus’ = 'REJECTED' > 'rewardsReceiptStatus’ = 'ACCEPTED'.

In [14]:
query = """
SELECT
    CASE 
        WHEN rewardsReceiptStatus IN ('FINSIHED', 'SUBMITTED', 'FLAGGED', 'PENDING') AND pointsAwardedDate IS NOT NULL THEN 'Accepted'
        WHEN rewardsReceiptStatus = 'REJECTED' THEN 'Rejected'
    END AS receipt_status,
    ROUND(AVG(actual_finalPrice), 2) AS avg_spend
FROM
    receipts
WHERE
    (rewardsReceiptStatus IN ('FINSIHED', 'SUBMITTED', 'FLAGGED', 'PENDING') AND pointsAwardedDate IS NOT NULL)
    OR rewardsReceiptStatus = 'REJECTED'
GROUP BY
    receipt_status;
"""
result = pd.read_sql_query(query, conn)
#result = result.drop_duplicates()
#result.to_excel('output.xlsx')
# Print the result of the query
print(len(result))
print(result)

2
  receipt_status  avg_spend
0       Accepted       4.74
1       Rejected      24.37


4] When considering total number of items purchased from receipts with 'rewardsReceiptStatus’ of ‘Accepted’ or ‘Rejected’, which is greater?
- Below query retrieves the status of receipts and the total number of items purchased for each receipt status.
- The logic here is: receipt_status:
If the rewardsReceiptStatus is one of FINISHED, SUBMITTED, FLAGGED, or PENDING and pointsAwardedDate is not NULL, it is labeled as 'Accepted'.
If rewardsReceiptStatus is 'REJECTED', it is labeled as 'Rejected'.
- Here I have calculated the total sum of the quantity of items purchased for each receipt status. To do so, a new column is created 'actual_purchasedItemCount' in the RECEIPTS table which maps the data correctly with the ITEMS table.
- To answer the question here, the total number of items purchased from receipts with 'rewardsReceiptStatus’ = 'REJECTED' > 'rewardsReceiptStatus’ = 'ACCEPTED'.

In [15]:
query = """
SELECT
    CASE 
        WHEN rewardsReceiptStatus IN ('FINSIHED', 'SUBMITTED', 'FLAGGED', 'PENDING') AND pointsAwardedDate IS NOT NULL THEN 'Accepted'
        WHEN rewardsReceiptStatus = 'REJECTED' THEN 'Rejected'
    END AS receipt_status,
    SUM(actual_purchasedItemCount) AS TotalItems
FROM
    receipts 
WHERE
    (rewardsReceiptStatus IN ('FINSIHED', 'SUBMITTED', 'FLAGGED', 'PENDING') AND pointsAwardedDate IS NOT NULL)
    OR rewardsReceiptStatus = 'REJECTED'
GROUP BY
    rewardsReceiptStatus
ORDER BY
    TotalItems DESC;
"""
result = pd.read_sql_query(query, conn)
#result = result.drop_duplicates()
#result.to_excel('output.xlsx')
# Print the result of the query
print(len(result))
print(result)

2
  receipt_status  TotalItems
0       Rejected       185.0
1       Accepted        42.0


5] Which brand has the most spend among users who were created within the past 6 months?
- Identifythe most recent month from the users table using the createdDate column.
- Filter users with the role "consumer" who were created within the last six months from the most recent month calculated earlier.
- Join the RecentUsers with the ITEMS and BRANDS table to gather item details for the filtered users and calculate the total spending for each brand.
- Finally the query retrieves the brand with the highest total spending. 

In [16]:
query = """
WITH MostRecentMonth AS (
    SELECT
        MAX(strftime('%Y-%m', createdDate) || '-01') AS recent_month
    FROM
        users
),
RecentUsers AS (
    SELECT
        userId
    FROM
        users
    WHERE
        createdDate >= date((SELECT recent_month FROM MostRecentMonth), '-6 months')
    AND role = 'consumer'
),
BrandSpend AS (
    SELECT
        i.rewardsProductPartnerId AS brand_id,
        b.name AS brand_name,
        SUM(i.finalPrice) AS total_spend
    FROM
        RecentUsers r
    JOIN
        items i
    ON
        r.userId = i.userId
    JOIN
        brands b
    ON
        i.rewardsProductPartnerId = b.cpg_id
    GROUP BY
        i.rewardsProductPartnerId, b.name
)
SELECT
    brand_name,
    total_spend
FROM
    BrandSpend
ORDER BY
    total_spend DESC
LIMIT 1
;
"""

result = pd.read_sql_query(query, conn)
#result = result.drop_duplicates()
#result.to_excel('output.xlsx')
# Print the result of the query
print(len(result))
print(result)

1
  brand_name  total_spend
0       A.1.      4630.18


6] Which brand has the most transactions among users who were created within the past 6 months?
- Identify the most recent month from the users table using the createdDate column.
- Filter users with the role "consumer" who were created within the last six months from the most recent month calculated earlier.
- Join the RecentUsers with the ITEMS and bRANDS table to gather receipt details for the filtered users and calculate the number of transactions for each brand.
- Finally the query retrieves the brand with the highest transaction count.

In [17]:
query = """
WITH MostRecentMonth AS (
    SELECT
        MAX(strftime('%Y-%m', createdDate) || '-01') AS recent_month
    FROM
        users
),
RecentUsers AS (
    SELECT
        userId
    FROM
        users
    WHERE
        createdDate >= date((SELECT recent_month FROM MostRecentMonth), '-6 months')
    AND role = 'consumer'
),
BrandTransactions AS (
    SELECT
        b.name AS brand_name,
        COUNT(i.rewardsProductPartnerId) AS transaction_count
    FROM
        RecentUsers r
    JOIN
        items i
    ON
        r.userId = i.userId
    JOIN
        brands b
    ON
        i.rewardsProductPartnerId = b.cpg_id
    GROUP BY b.name
)
SELECT
    brand_name,
    transaction_count
FROM
    BrandTransactions
ORDER BY
    transaction_count DESC
LIMIT 1;
"""

result = pd.read_sql_query(query, conn)
#result = result.drop_duplicates()
#result.to_excel('output.xlsx')
# Print the result of the query
print(len(result))
print(result)

1
  brand_name  transaction_count
0       A.1.                641


STEP 4: Data Quality Issues

- Missing or Incomplete Data: Records with missing values for required fields in all the tables.
Solution: Removed all the null values in step 2.

- Inconsistent Data: Different formats, units, or terms being used for the same data.
Solution: Transformed all the columns to appropriate data type in step 2.

- Duplicate Data: Redundant records for the same entity.
Solution: Eliminated all duplicate records in each table based on their primary key. For example: In USERS table,removed rows with missing or duplicate userId values.

- Missing Relations between Tables: The user_id and receipt_id were missing in the reward items(nested column) in the RECEIPTS table, which made it difficult to establish a clear relationship between them. 
Solution: Added the user_id and receipt_id fields to each reward item, which simplified the relationships and facilitated more accurate table joins (performed in step 2-3.B).

- Data Integrity Issues: Broken relationships or incorrect links between data points.
Example: After creating a separate table for 'ITEMS' from 'RECEIPTS', I identified several null values and data redundancy. 
Additionally, many items in the item lists were not properly mapped to either the barcode or the receipt_id, making it challenging to join with the BRANDS table. Currently, the rewardsProductPartnerID column is being used, which matches the cpg_id, to establish the connection.

- Data Discrepancy: The purchasedItemCount column in the RECEIPTS table is inaccurate, as the itemCount for each receipt_id in the ITEMS table does not match. To address this issue, a new column(actual_purchasedItemCount) was added to the RECEIPTS table, which is correctly mapped by calculating the sum of quantityPurchased for each receipt_id.(refer step 2-4) If needed, we can also replace the original columns with new values instead of additional columns.

   Similary, the data values in 'totalSpent' column in RECEIPTS table is inaccurate, as it does not match the values in 'finalPrice' in ITEMS table. An additional column(actual_finalPrice) is created which correctly maps by calculating the sum of finalPrice for each receipt_id.(refer step 2-4)

- Rewards Table: If the use case is for storage purpose only then a separate Rewards table could help minimize the number of date columns in the fact table. Since in the current scenario, we are analyzing data so it makes most sense to have a consolidated metric table.

- Items table: The 'ITEMS' table currently has 34 columns, and it’s important to evaluate whether all of these columns are relevant. Keeping only the necessary columns would streamline the table and improve maintainability. For this business problem, I have dropped all the unnecessary columns. (refer step 2-4)

- Document the Changes: Maintained a record of the columns removed from ITEMS table to ensure transparency and accountability for future users or stakeholders.

STEP 5: Communicate with Stakeholder

##### Dear [Recipient/Team],

I hope this message finds you well. This is **Alisha Gonsalves**, and I have been analyzing the Fetch Rewards dataset to address key business questions and uncover actionable insights. During my analysis, I identified a few data quality issues and have some questions that I would appreciate your guidance on:

#### 1. Nested Data in RECEIPTS Table
The `rewardsReceiptItemList` column contains nested data, which consists of information about the items purchased for each receipt.

**Action Taken**:  
Extracted and reorganized the `rewardsReceiptItemList` column into a new `ITEMS` table to improve readability and analysis.

#### 2. Discrepancies in Data Values

- The `purchasedQuantity` in the `RECEIPTS` data does not align with the `SUM(itemQuantity)` for each `receipt_id` in the `ITEMS` data.  
- The `totalSpent` in the `RECEIPTS` data differs from the computed `finalPrice` for each `receipt_id` in the `ITEMS` data.  
- Additionally, the `item_price` appears to be incorrect as it matches the `finalPrice`, which suggests potential issues in the price logic.

**Action Taken**:  
Created additional columns for `purchasedQuantity` and `totalSpent` in the `RECEIPTS` table, mapping the correct computed values from the `ITEMS` table.

**Question**:  
Should the `itemPrice` always equal `finalPrice` in the `ITEMS` table, or is there a separate logic for price allocation that we are missing?

#### 3. Missing Values Across Schemas
Incomplete or missing data in critical columns of the `RECEIPTS` schema could compromise the accuracy of insights.

**Action Taken**:  
Performed data cleaning on the table.

**Questions**:  
Are the incomplete or missing values in the `RECEIPTS` schema expected due to challenges faced in extracting data during receipt image processing submitted by the user?

#### 4. Lack of Relationship between BRAND & RECEIPTS Data
The `BRAND` data currently lacks defined primary key-foreign key relationships. This limitation prevents it from being effectively linked to other tables, which is crucial for creating meaningful connections across datasets.

**Action Taken**:  
Defined a relationship between `BRANDS'(cpg_id) and `ITEMS`(rewardsProductPartnerId) to create a connection with the `RECEIPTS` data for analysis purposes.

**Questions**:  
1. Why does the `BRAND` table lack relationships between the data? Why do we not have `brand_id` information in the `ITEMS` data?
2. Can you confirm the correct relationship to ensure accurate linking between the `BRAND` and `ITEMS` tables?

#### 5. Additional Schemas
Are there any other schemas or tables associated with this use case that could provide better clarity on data relationships or enhance our ability to address the business problem effectively? If so, could you share insights into their structure and relevance?

#### Performance and Scaling Concerns

Here are four concise performance and scaling concerns to anticipate:

1. **Query Performance**: Complex queries & joins may slow down due to the expanded data structure.  
   **Plan**: Optimize queries with indexing, materialized views, and breaking down complex joins.

2. **Data Growth**: Larger datasets may affect storage and processing.  
   **Plan**: Partition data and use cloud infrastructure for scaling.

3. **Data Integrity**: Discrepancies may lead to data quality issues.  
   **Plan**: Implement validation checks.

4. **Concurrency**: Multiple users may cause load issues.  
   **Plan**: Use load balancing and caching for frequently accessed data.

5. **System Scalability**: Scaling to support new use cases and larger workloads.  
   **Plan**: Use distributed frameworks for big data processing.

Your insights on these questions would help in optimizing the data model and ensuring the dataset is more efficient for analysis. Please let me know if a discussion would be helpful or if you need any additional information from my end.

Looking forward to your guidance!

Regards,  
**Alisha Gonsalves**
